# Homework 5: Model Selection and Extreme Values

BEE 4850/5850, Spring 2025

**Name**:

**ID**:

> **Due Date**
>
> Friday, 5/2/25, 9:00pm

## Overview

### Instructions

The goal of this homework assignment is to practicing approaches to
extreme value analysis and using information criteria to assess evidence
for models.

-   Problem 1 asks you to compare stationary and non-stationary block
    maxima models for daily maximum temperature data.
-   Problem 2 asks you to use peaks-over-thresholds modeling on the same
    dataset from Problem 1.
-   Problem 3 (only required for students in BEE 5850) asks you to
    compare several linear regression models for environmental
    influences on non-accidental death data.

### Load Environment

The following code loads the environment and makes sure all needed
packages are installed. This should be at the start of most Julia
scripts.

In [1]:
import Pkg
Pkg.activate(@__DIR__)
Pkg.instantiate()

The following packages are included in the environment (to help you find
other similar packages in other languages). The code below loads these
packages for use in the subsequent notebook (the desired functionality
for each package is commented next to the package).

In [1]:
using Random # random number generation and seed-setting
using DataFrames # tabular data structure
using DataFramesMeta # API which can simplify chains of DataFrames transformations
using CSV # reads/writes .csv files
using Distributions # interface to work with probability distributions
using Plots # plotting library
using StatsBase # statistical quantities like mean, median, etc
using StatsPlots # some additional statistical plotting tools
using Dates

## Problems

### Scoring

-   Problem 1 is worth 10 points;
-   Problem 2 is worth 10 points;
-   Problem 3 is worth 5 points;

### Problem 1

Let’s look at how (modeled) annual maximum temperatures have (or have
not) increased in Ithaca from 1850–2014. Model output from NOAA’s
GFDL-ESM4 climate model (one of the models used in the latest Climate
Model Intercomparison Project,
[CMIP6](https://colab.research.google.com/corgiredirector?site=https%3A%2F%2Fcds.climate.copernicus.eu%2Fcdsapp%23%21%2Fdataset%2Fprojections-cmip6%3Ftab%3Doverview))
is available in `data/gfdl-esm4-tempmax-ithaca.csv`. While this model
output has not been bias-corrected, we won’t worry about that for the
purposes of this assignment. The temperature data is in degrees Celsius,
and the dates are provided as calendar dates.

In [1]:
ithaca_dat = CSV.read("data/gfdl-esm4-tempmax-ithaca.csv", DataFrame)
plot(ithaca_dat.Day, ithaca_dat.TempMax, lw=2, xlabel="Date", ylabel="Daily Maximum Temperature (°C)", legend=false)

<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 <path clip-path="url(#clip500)" d="M168.426 1782.41 Q165.092 1782.41 163.171 1784.19 Q161.273 1785.97 161.273 1789.1 Q161.273 1792.22 163.171 1794.01 Q165.092 1795.79 168.426 1795.79 Q171.759 1795.79 173.68 1794.01 Q175.602 1792.2 175.602 1789.1 Q175.602 1785.97 173.68 1784.19 Q171.782 1782.41 168.426 1782.41 M163.75 1780.42 Q160.741 1779.68 159.051 1777.62 Q157.384 1775.56 157.384 1772.59 Q157.384 1768.45 160.324 1766.04 Q163.287 1763.64 168.426 1763.64 Q173.588 1763.64 176.528 1766.04 Q179.467 1768.45 179.467 1772.59 Q179.467 1775.56 177.778 1777.62 Q176.111 1779.68 173.125 1780.42 Q176.504 1781.21 178.379 1783.5 Q180.277 1785.79 180.277 1789.1 Q180.277 1794.12 177.199 1796.81 Q174.143 1799.49 168.426 1799.49 Q162.708 1799.49 159.629 1796.81 Q156.574 1794.12 156.574 1789.1 Q156.574 1785.79 158.472 1783.5 Q160.37 1781.21 163.75 1780.42 M162.037 1773.03 Q162.037 1775.72 163.704 1777.22 Q165.393 1778.73 168.426 1778.73 Q171.435 1778.73 173.125 1777.22 Q174.838 1775.72 174.838 1773.03 Q174.838 1770.35 173.125 1768.84 Q171.435 1767.34 168.426 1767.34 Q165.393 1767.34 163.704 1768.84 Q162.037 1770.35 162.037 1773.03 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /> <path clip-path="url(#clip500)" d="M229.328 1779.68 Q226.18 1779.68 224.328 1781.83 Q222.499 1783.98 222.499 1787.73 Q222.499 1791.46 224.328 1793.64 Q226.18 1795.79 229.328 1795.79 Q232.476 1795.79 234.305 1793.64 Q236.157 1791.46 236.157 1787.73 Q236.157 1783.98 234.305 1781.83 Q232.476 1779.68 229.328 1779.68 M238.611 1765.02 L238.611 1769.28 Q236.851 1768.45 235.046 1768.01 Q233.263 1767.57 231.504 1767.57 Q226.874 1767.57 224.421 1770.7 Q221.99 1773.82 221.643 1780.14 Q223.009 1778.13 225.069 1777.06 Q227.129 1775.97 229.606 1775.97 Q234.814 1775.97 237.823 1779.15 Q240.856 1782.29 240.856 1787.73 Q240.856 1793.06 237.708 1796.27 Q234.56 1799.49 229.328 1799.49 Q223.333 1799.49 220.162 1794.91 Q216.99 1790.3 216.99 1781.58 Q216.99 1773.38 220.879 1768.52 Q224.768 1763.64 231.319 1763.64 Q233.078 1763.64 234.861 1763.98 Q236.666 1764.33 238.611 1765.02 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /> <path clip-path="url(#clip500)" d="M276.018 1767.34 Q272.407 1767.34 270.578 1770.9 Q268.772 1774.45 268.772 1781.58 Q268.772 1788.68 270.578 1792.25 Q272.407 1795.79 276.018 1795.79 Q279.652 1795.79 281.458 1792.25 Q283.286 1788.68 283.286 1781.58 Q283.286 1774.45 281.458 1770.9 Q279.652 1767.34 276.018 1767.34 M276.018 1763.64 Q281.828 1763.64 284.883 1768.24 Q287.962 1772.83 287.962 1781.58 Q287.962 1790.3 284.883 1794.91 Q281.828 1799.49 276.018 1799.49 Q270.208 1799.49 267.129 1794.91 Q264.073 1790.3 264.073 1781.58 Q264.073 1772.83 267.129 1768.24 Q270.208 1763.64 276.018 1763.64 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /> <path clip-path="url(#clip500)" d="M353.448 1767.34 Q349.837 1767.34 348.008 1770.9 Q346.203 1774.45 346.203 1781.58 Q346.203 1788.68 348.008 1792.25 Q349.837 1795.79 353.448 1795.79 Q357.082 1795.79 358.888 1792.25 Q360.716 1788.68 360.716 1781.58 Q360.716 1774.45 358.888 1770.9 Q357.082 1767.34 353.448 1767.34 M353.448 1763.64 Q359.258 1763.64 362.314 1768.24 Q365.392 1772.83 365.392 1781.58 Q365.392 1790.3 362.314 1794.91 Q359.258 1799.49 353.448 1799.49 Q347.638 1799.49 344.559 1794.91 Q341.503 1790.3 341.503 1781.58 Q341.503 1772.83 344.559 1768.24 Q347.638 1763.64 353.448 1763.64 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /> <path clip-path="url(#clip500)" d="M770.696 1782.41 Q767.363 1782.41 765.442 1784.19 Q763.543 1785.97 763.543 1789.1 Q763.543 1792.22 765.442 1794.01 Q767.363 1795.79 770.696 1795.79 Q774.03 1795.79 775.951 1794.01 Q777.872 1792.2 777.872 1789.1 Q777.872 1785.97 775.951 1784.19 Q774.053 1782.41 770.696 1782.41 M766.02 1780.42 Q763.011 1779.68 761.321 1777.62 Q759.655 1775.56 759.655 1772.59 Q759.655 1768.45 762.594 1766.04 Q765.557 1763.64 770.696 1763.64 Q775.858 1763.64 

**In this problem**:

-   Load the (daily maximum) temperature data from
    `data/gfdl-esm4-tempmax-ithaca.csv`. Find the modeled annual maximum
    temperatures and plot them.
-   Fit a stationary GEV model to the annual maximum series and report
    your parameter estimates. Plot the fitted distribution along with
    the data. What type of GEV distribution did you end up with? What is
    the 100-year return level?
-   Now fit a nonstationary GEV with respect to time (only the location
    parameter should be non-stationary),
    $y \sim \text{GEV}(\mu_0 + \mu_1 t, \sigma, \xi)$ (for scaling
    purposes, begin with $t=0$ corresponding to 1850).
-   What are the AIC values for each model? What can you conclude about
    the relative evidence for non-stationarity?

### Problem 2

Now let’s analyze how often of the Ithaca temperature data.

**In this problem**:

-   Suppose that we were interested in looking at temperature
    exceedances over 28°C. Decluster these occurrences and plot the
    number of exceedances by year. Have they increased over time?
-   Fit a stationary Poisson-GPD model for the exceedances. What does
    the GPD distribution look like?
-   From your model, estimate the 100-year return level. How does it
    differ from the 100-year return period from the stationary model in
    Problem 1? Why do you think it agrees or disagrees?

### Problem 3

**This problem is only required for students in BEE 5850**.

Let’s examine the influence of air pollution and temperature on
mortality in Chicago, IL. The `data/chicago.csv` dataset (originally
from the [`gamair` `R`
package](https://cran.r-project.org/web/packages/gamair/index.html))contains
data on the relationship between environmental conditions (temperature
and air quality) and deaths in Chicago from 1987–2000. The variables
are:

-   the total number of (non-accidental) deaths each day (`death`);
-   the median density over the city of large pollutant particles (PM10;
    `pm10median`);
-   the median density of smaller pollutant particles (PM2.5;
    `pm25median`);
-   the median concentration of ozone (O$_3$) in the air (`o3median`);
    the median concentration of sulfur dioxide (SO$_2$) in the air
    (`so2median`);
-   the time in days (`time`); and the daily mean temperature (`tmpd`).

The pollution variables have been standardized to represent deviations
from the overall median and the temperature is in Fahrenheit. The days
are given as a number of days relative to December 31, 1993. Note that
some values are missing; these can be treated as missing at random and
dropped in your regressions.

In [1]:
chicago_dat = CSV.read("data/chicago.csv", DataFrame; delim=',', header=true, missingstring="NA")
day_zero = Date("1993-12-31")
chicago_dat.Date = day_zero .+ Day.(chicago_dat.time .+ 0.5)

plot(chicago_dat.Date, chicago_dat.death, lw=2, xlabel="Date", ylabel="Non-Accidental Deaths)", legend=false)

<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 <path clip-path="url(#clip560)" d="M206.659 1798.1 L206.659 1793.84 Q208.418 1794.68 210.223 1795.12 Q212.029 1795.56 213.765 1795.56 Q218.395 1795.56 220.825 1792.46 Q223.279 1789.33 223.626 1782.99 Q222.284 1784.98 220.223 1786.04 Q218.163 1787.11 215.663 1787.11 Q210.478 1787.11 207.446 1783.98 Q204.436 1780.83 204.436 1775.4 Q204.436 1770.07 207.585 1766.85 Q210.733 1763.64 215.964 1763.64 Q221.959 1763.64 225.108 1768.24 Q228.279 1772.83 228.279 1781.58 Q228.279 1789.75 224.39 1794.63 Q220.524 1799.49 213.973 1799.49 Q212.214 1799.49 210.409 1799.15 Q208.603 1798.8 206.659 1798.1 M215.964 1783.45 Q219.112 1783.45 220.941 1781.3 Q222.793 1779.15 222.793 1775.4 Q222.793 1771.67 220.941 1769.52 Q219.112 1767.34 215.964 1767.34 Q212.816 1767.34 210.964 1769.52 Q209.135 1771.67 209.135 1775.4 Q209.135 1779.15 210.964 1781.3 Q212.816 1783.45 215.964 1783.45 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip560)" d="M246.682 1782.41 Q243.348 1782.41 241.427 1784.19 Q239.529 1785.97 239.529 1789.1 Q239.529 1792.22 241.427 1794.01 Q243.348 1795.79 246.682 1795.79 Q250.015 1795.79 251.936 1794.01 Q253.857 1792.2 253.857 1789.1 Q253.857 1785.97 251.936 1784.19 Q250.038 1782.41 246.682 1782.41 M242.006 1780.42 Q238.996 1779.68 237.307 1777.62 Q235.64 1775.56 235.64 1772.59 Q235.64 1768.45 238.58 1766.04 Q241.543 1763.64 246.682 1763.64 Q251.844 1763.64 254.783 1766.04 Q257.723 1768.45 257.723 1772.59 Q257.723 1775.56 256.033 1777.62 Q254.367 1779.68 251.381 1780.42 Q254.76 1781.21 256.635 1783.5 Q258.533 1785.79 258.533 1789.1 Q258.533 1794.12 255.455 1796.81 Q252.399 1799.49 246.682 1799.49 Q240.964 1799.49 237.885 1796.81 Q234.83 1794.12 234.83 1789.1 Q234.83 1785.79 236.728 1783.5 Q238.626 1781.21 242.006 1780.42 M240.293 1773.03 Q240.293 1775.72 241.959 1777.22 Q243.649 1778.73 246.682 1778.73 Q249.691 1778.73 251.381 1777.22 Q253.094 1775.72 253.094 1773.03 Q253.094 1770.35 251.381 1768.84 Q249.691 1767.34 246.682 1767.34 Q243.649 1767.34 241.959 1768.84 Q240.293 1770.35 240.293 1773.03 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /> <path clip-path="url(#clip560)" d="M324.112 1767.34 Q320.501 1767.34 318.672 1770.9 Q316.866 1774.45 316.866 1781.58 Q316.866 1788.68 318.672 1792.25 Q320.501 1795.79 324.112 1795.79 Q327.746 1795.79 329.551 1792.25 Q331.38 1788.68 331.38 1781.58 Q331.38 1774.45 329.551 1770.9 Q327.746 1767.34 324.112 1767.34 M324.112 1763.64 Q329.922 1763.64 332.977 1768.24 Q336.056 1772.83 336.056 1781.58 Q336.056 1790.3 332.977 1794.91 Q329.922 1799.49 324.112 1799.49 Q318.302 1799.49 315.223 1794.91 Q312.167 1790.3 312.167 1781.58 Q312.167 1772.83 315.223 1768.24 Q318.302 1763.64 324.112 1763.64 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /> <path clip-path="url(#clip560)" d="M401.542 1767.34 Q397.931 1767.34 396.102 1770.9 Q394.296 1774.45 394.296 1781.58 Q394.296 1788.68 396.102 1792.25 Q397.931 1795.79 401.542 1795.79 Q405.176 1795.79 406.982 1792.25 Q408.81 1788.68 408.81 1781.58 Q408.81 1774.45 406.982 1770.9 Q405.176 1767.34 401.542 1767.34 M401.542 1763.64 Q407.352 1763.64 410.408 1768.24 Q413.486 1772.83 413.486 1781.58 Q413.486 1790.3 410.408 1794.91 Q407.352 1799.49 401.542 1799.49 Q395.732 1799.49 392.653 1794.91 Q389.597 1790.3 389.597 1781.58 Q389.597 1772.83 392.653 1768.24 Q395.732 1763.64 401.542 1763.64 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /> <path clip-path="url(#clip560)" d="M853.406 1798.1 L853.406 1793.84 Q855.165 1794.68 856.971 1795.12 Q858.776 1795.56 860.513 1795.56 Q865.142 1795.56 867.573 1792.46 Q870.026 1789.33 870.374 1782.99 Q869.031 1784.98 866.971 1786.04 Q864.911 1787.11 862.411 1787.11 Q857.226 1787.11 854.193 1783.98 Q851.184 1780.83 851.184 1775.4 Q851.184 1770.07 854.332 1766.85 Q857.48 1763.64 862.712 1763.64 Q868.707 1763.64 871.855 1768.24 Q875.026 1772.83 875.026 1781.58 Q875.026 1789.75 871.138 1794

**In this problem**:

-   Load and plot the deaths data. Linearly regress the number of deaths
    against time and report the coefficients for the fitted model. Add
    the regression line to your plot. What does this regression tell
    you?
-   Now linearly regress the deaths data against temperature. Once
    again, report the coefficients, and add the regression line to your
    plot. What does this regression tell you about the influence of
    temperature?
-   Expand your previous model by regressing deaths against temperature
    and PM2.5 density. Report the coefficients and add this regression
    line to your plot.
-   Compute the AICs for the three fitted model and compare them. What
    do they tell you about the relative evidence for the influence of
    temperature and PM2.5 density on deaths? How do your conclusions
    based on AIC compare to those you might draw from your regression
    coefficients and plots?